<a href="https://colab.research.google.com/github/JIRUWANG1997/-keras-stacking-keras-with-tf2.0/blob/master/Untitled9.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
pip install patool

In [ ]:
import patoolib
patoolib.extract_archive("/content/lemm_stop.rar", outdir="/content/sample_data")

In [ ]:
import os
import glob
import re
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer
from tkinter import _flatten
import math
import numpy as np
import random


##### **Parameter**:  
dir:  file name for part1~10  
##### **Function**:
For all the .txt files in one part file, split spam and legit files
##### **return**:
spam and legit files in part1 or part2 or...

In [ ]:
def get_data(dir):
  content_legit = []
  content_spam = []
  legit_mails = glob.glob("/content/sample_data/lemm_stop/" + dir + "/*msg?.txt")
  spam_mails = glob.glob("/content/sample_data/lemm_stop/" + dir + "/spmsg*.txt")
  for legit_mail in legit_mails:
    f_legit = open(legit_mail, "r")
    each_mail = ""
    for idx,eachLine in enumerate(f_legit):
      if eachLine == "\n":
        continue
      # print(each_mail)
      each_mail+= eachLine.lower() 
    content_legit.append(each_mail)
  for spam_mail in spam_mails:
    f_spam = open(spam_mail, "r")
    each_mail = ""
    for idx,eachLine in enumerate(f_spam):
      if eachLine == "\n":
        continue
      each_mail+= eachLine.lower()
    content_spam.append(each_mail)
  # print(len(content_spam))
  # print(len(content_legit))
  return content_spam,content_legit

In [ ]:
''' TEST  '''
# x,y = get_data("part9")
# print(x[10])
# print(len(y))
# # print(y[10])

' TEST  '

##### **Parameter**:  
dataset_dir:  lemm_stop
##### **Function**:
build train and test dataset
##### **return**:
train_x, train_y, test_x, test_y

In [ ]:
def split_test_train(dataset_dir):
  print('Loading dataset')
  f = os.listdir(dataset_dir)
  train_data = []
  train_class = []
  test_data = []
  test_class = []
  for file_name in f:
    if file_name != "part10":
      spam_mail, legit_mail = get_data(file_name)
      print(len(spam_mail),len(legit_mail))
      train_data += spam_mail
      n = [1 for i in range(len(spam_mail))]
      train_class += n
      train_data += legit_mail
      n = [0 for i in range(len(legit_mail))]
      train_class+=n
      # print(len(train_data))
    else:
      spam_mail, legit_mail = get_data(file_name)
      # print(len(spam_mail))
      # print(len(legit_mail))
      test_data+=spam_mail
      n = [1 for i in range(len(spam_mail))]
      test_class+=n
      test_data+=legit_mail
      n = [0 for i in range(len(legit_mail))]
      test_class+=n

  return train_data,train_class,test_data,test_class

In [ ]:
train_data,train_class,test_data,test_class = split_test_train("/content/sample_data/lemm_stop/")
# print(len(train_data))
# print(len(test_data))

Loading dataset
48 241
48 241
48 241
48 242
48 241
48 241
48 241
48 241
48 241


##### **function**:
split word in train/test dataset

In [ ]:
def get_word_token(data):
  vectorizer = CountVectorizer(binary = True) 
  word_tokenizer = vectorizer.build_tokenizer()
  token = [word_tokenizer(doc_str) for doc_str in data]
  # print(len(token))
  return token

In [ ]:
train_data_token = get_word_token(train_data)

In [ ]:
test_data_token = get_word_token(test_data)

##### **function**:
build vocab, assign a single id for each word

In [ ]:
#assign a single id for each word
def get_term_dict(doc_terms_list):
  term_set_dict = {}
  for doc_terms in doc_terms_list:
    for term in doc_terms:
        term_set_dict[term] = 1
        # print(term_set_dict)
  term_set_list = sorted(term_set_dict.keys()) 
  # print(term_set_list)      
  term_set_dict = dict(zip(term_set_list, range(len(term_set_list))))
  return term_set_dict

In [ ]:
'''  Test  '''
# corpus = [
# 'This is the first document.',
# 'This is the second second document.',
# 'And the third one.',
# 'Is this the first document?',
#  ]
 
# f = get_term_dict(get_word_token(corpus))
# print(f)
# f = get_term_dict(train_data)
# print(f)

'  Test  '

In [ ]:
def get_class_dict(doc_class_list):
  class_dict = {}
  class_dict[0] = doc_class_list.count(0)
  class_dict[1] = doc_class_list.count(1)
  return class_dict

In [ ]:
vocab_dict = get_term_dict(train_data_token)
# class_dict = get_class_dict(train_class)
# print(class_dict)
# print(vocab_dict)


##### **function**:

compute frequency for spam and legit files

In [ ]:
def compute_frequency(train_data_token,train_class):
  c ={'x':train_data_token,'y':train_class}
  df = pd.DataFrame(c)
  from sklearn.utils import shuffle
  df = shuffle(df)
  vocab_dict = get_term_dict(train_data_token)#achieve word id
  
  #get spam
  df1 = df.loc[df['y']==1]
  spam_num = df1.shape[0]
  # print(spam_num)
  spams = df1['x'].values.tolist()
  # print(len(spams))
  spams_dict = set(_flatten(spams))
  # print(len(spams_dict))
  #get legit
  df0 = df.loc[df['y']==0]
  legit_num = df0.shape[0]
  legits = df0['x'].values.tolist()
  # print(legits)
  legits_dict = set(_flatten(legits))
  # print(len(legits_dict))
  
  vocab_spam = {}
  vocab_legit = {}
  #compute spam
  for word in spams_dict:
    # print(word)
    for spam in spams:
      if word in spam:
        vocab_spam[word] = vocab_spam.get(word, 0) + 1
  print(vocab_spam)
  for word in legits_dict:
    # print(word)
    for legit in legits:
      if word in legit:
        vocab_legit[word] = vocab_legit.get(word, 0) + 1
  
  print(vocab_legit)
  return spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit

In [ ]:
spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit = compute_frequency(train_data_token,train_class)


{'theater': 4, 'saunter': 1, 'bunny': 1, '32609': 1, 'est': 5, 'air08': 1, 'divorce': 9, 'universe': 2, 'placement': 2, 'fatty': 1, 'bud': 2, 'calculation': 1, 'former': 3, 'dudes': 2, 'mrbrutals': 1, 'often': 10, 'attend': 7, 'simon': 1, 'fatigue': 1, 'rate': 80, 'floodgate': 5, 'petition': 1, 'suprise': 1, 'wrap': 23, 'london': 12, 'buckley': 7, 'noticed': 1, 'separate': 13, 'breakup': 1, 'hills': 2, 'sock': 3, 'radio': 20, 'benidorm': 1, 'bookkeep': 1, 'unbelievably': 4, '97333': 1, 'confirmation': 4, 'tsb': 2, 'cyber3': 2, 'vow': 1, 'crown': 3, 'dialing': 1, 'ia': 1, '3xd': 2, 'confrontational': 2, 'lovemore': 1, 'serious': 20, 'hype': 4, '584': 1, 'havens': 1, 'dial': 13, '5854': 1, 'brave': 3, 'quicktime': 2, 'ntr': 1, 'pmail': 1, 'coulduse': 1, 'debt': 39, 'uncover': 3, 'corporations': 21, 'cbt': 2, 'planner': 1, 'paul': 17, 'jame': 2, 'keep': 91, 'earn': 64, 'depending': 1, 'patent': 8, 'egotistical': 1, 'itc': 3, 'energy': 10, 'wholeness': 1, 'spee': 4, '2gb': 1, 'nile': 1, 'w

In [ ]:
spam_num_t,legit_num_t,vocab_dict_t,vocab_spam_t,vocab_legit_t = compute_frequency(test_data_token,test_class)


{'theater': 1, 'distance': 1, 'trafford': 1, 'probe': 1, 'actually': 1, 'sirus': 1, 'morissette': 1, 'activity': 3, 'c70': 1, 'tomorrow': 1, 'point': 3, 'removal': 1, 'eager': 1, 'owe': 1, '60': 3, 'gino': 1, 'former': 1, 'four': 4, 'sudden': 1, '100': 9, 'often': 1, 'attend': 1, 'enough': 1, 'private': 2, 'selle': 3, 'simon': 1, 'wake': 1, 'rate': 2, 'moment': 3, 'lindsay': 3, 'zileus': 1, 'thru': 1, 'regreta': 1, 'shout': 1, 'icely': 1, 'si': 1, 'london': 4, 'ac': 1, 'seller': 1, 'arena': 1, 'part': 8, 'center': 1, 'card': 4, 'arr': 1, 'a0from': 1, 'radio': 5, 'memorabilia': 2, 'busness': 1, 'result': 4, 'nott': 1, 'additional': 2, '2000': 2, 'material': 1, 'naturally': 1, 'mean': 1, 'confirmation': 1, 'ce': 1, 'foreplay': 1, 'return': 6, 'shtml': 1, 'vote': 2, 'sweepstake': 1, 'consumer': 1, 'better': 5, '1st': 2, '7086': 1, 'favorite': 2, 'serious': 2, 'ok': 1, 'com': 27, 'walk': 4, 'akron': 1, 'distributor': 2, '50p': 2, 'contribution': 1, 'juventus': 1, 'bid': 4, '92s': 1, 'lug':

In [ ]:
print(spam_num,legit_num)
print(vocab_dict)
print(vocab_spam)
print(vocab_legit)

432 2170
{'00': 0, '000': 1, '00003000140': 2, '00003003958': 3, '0001': 4, '00014': 5, '00036': 6, '000bp': 7, '000yen': 8, '001': 9, '0011': 10, '0014': 11, '00170': 12, '0019': 13, '00198': 14, '0027': 15, '0031': 16, '00333': 17, '0037': 18, '0039': 19, '003n7': 20, '0041': 21, '0049': 22, '0057': 23, '0067': 24, '0073': 25, '0074': 26, '008': 27, '009': 28, '00919680': 29, '00a': 30, '00am': 31, '00congress': 32, '00d': 33, '00f': 34, '00h': 35, '00hfstahlke': 36, '00i': 37, '00p': 38, '00pm': 39, '00the': 40, '00uzheb': 41, '01': 42, '01006': 43, '0106': 44, '0108': 45, '011': 46, '0118': 47, '01232': 48, '0135': 49, '0139': 50, '013953': 51, '013a': 52, '014686': 53, '0147': 54, '014796': 55, '014863': 56, '014893': 57, '014904': 58, '014979': 59, '014991': 60, '015491': 61, '015509': 62, '015679': 63, '015780': 64, '015820': 65, '016086': 66, '0161': 67, '016187': 68, '016197': 69, '016285': 70, '01701': 71, '0177': 72, '01784': 73, '0181': 74, '0182': 75, '01904': 76, '01bd835

In [ ]:
print(len(vocab_dict))
print(len(vocab_spam))
print(len(vocab_legit))


51602
9998
47487


##### **function**:
compute IG for each word

In [ ]:
def compute_IG_word(word,spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit):
  if word in vocab_spam.keys():
    s = vocab_spam[word]
  else:
    s = 0
  if word in vocab_legit.keys():
    l = vocab_legit[word]
  else:
    l = 0
  total = spam_num+legit_num
  # print(vocab_spam[word])#4
  # print(vocab_legit[word])#51
  # print(spam_num+legit_num)#2602
  if s == 0:
    A=0
  else:
    A = (s/total)*(math.log(s/(s+l)))#spam&present:0.0060741640562358605
  # print(A)
  if (spam_num-s == 0) or (total-s-l == 0):
    B = 0
  else:
    B = ((spam_num-s)/(total))*(math.log((spam_num-s)/(total-s-l)))
  # print(B)
  if l == 0:
    C = 0
  else:
    C = (l/total)*(math.log(l/(s+l)))
  # print(C)
  if (legit_num-l==0) or (total-s-l==0):
    D = 0
  else:
    D = ((legit_num-l)/(total))*(math.log((legit_num-l)/(total-s-l)))
  # print(D)
  return -(A+B+C+D)

In [ ]:
# IG_for_word = compute_IG_word('slowly',432,2170,vocab_dict,vocab_spam,vocab_legit)
# print(IG_for_word)

In [ ]:
def compute_IG_dict(spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit):
  res = {}
  for word in vocab_dict.keys():
    res[word] = compute_IG_word(word,spam_num,legit_num,vocab_dict,vocab_spam,vocab_legit)
    
  res = sorted(res.items(), key = lambda item:item[1])
  
  # print(res)

  return res

In [ ]:
IG_dict = compute_IG_dict(432,2170,vocab_dict,vocab_spam,vocab_legit)
print(IG_dict)

[('language', 0.3067603560254749), ('remove', 0.33243051762615417), ('free', 0.33642552041112483), ('linguistic', 0.3433256804175116), ('university', 0.3490178273004656), ('money', 0.36726795765267584), ('click', 0.37864945333327626), ('market', 0.38540704032399575), ('our', 0.3879838770047447), ('business', 0.3893441762896718), ('today', 0.3931140202836582), ('advertise', 0.3954411338916085), ('product', 0.3959467050053215), ('company', 0.39616305584116357), ('sell', 0.3962663922243214), ('million', 0.3974351109752905), ('linguistics', 0.39748227048158463), ('english', 0.39772715090031996), ('internet', 0.39786042273675437), ('income', 0.39885109841613664), ('easy', 0.40046729654956076), ('save', 0.401494145912721), ('guarantee', 0.4018832858657611), ('thousand', 0.4020699667184648), ('best', 0.4035228519134786), ('check', 0.40385282536068023), ('purchase', 0.40460054460748196), ('buy', 0.4050977583294578), ('cash', 0.4052741864952597), ('win', 0.4053364428885521), ('day', 0.405850876

In [ ]:
IG_dict_t = compute_IG_dict(spam_num_t,legit_num_t,vocab_dict_t,vocab_spam_t,vocab_legit_t)
print(IG_dict_t)

[('language', 0.25976061826519964), ('1998', 0.25992239124260613), ('university', 0.2742699003556051), ('linguistic', 0.3296946867866638), ('papers', 0.3508449610787564), ('conference', 0.35200929930266955), ('remove', 0.3674456586948345), ('research', 0.3783152679167061), ('english', 0.3797406303672646), ('study', 0.38072054255747034), ('author', 0.38553580194626547), ('wait', 0.38749392632250457), ('click', 0.3883823477702234), ('ll', 0.38892037166257126), ('workshop', 0.3911369540062285), ('abstract', 0.3929631108191859), ('sell', 0.39342193774565093), ('never', 0.39394217628871575), ('committee', 0.3947695619433619), ('discussion', 0.3947695619433619), ('enter', 0.3956690244332387), ('vacation', 0.3956690244332387), ('com', 0.3980090496772769), ('free', 0.39856162698453756), ('want', 0.3989135806219429), ('save', 0.39951176498810603), ('deadline', 0.4000748450991357), ('speaker', 0.4000748450991357), ('fax', 0.4009363090867062), ('structure', 0.4009429464884674), ('everyone', 0.402

**feature extraction and embedding**

In [406]:

feature_nums = [10, 100, 1000]
feature = []
for i in IG_dict:
  feature.append(i[0])
print(feature)
features = [0] * len(feature_nums)
print(features)
c = 0
for feature_num in feature_nums:
  features[c] = feature[:feature_num]
  c += 1
print(features[0])
print(features[1])
print(features[2]) 


['language', 'remove', 'free', 'linguistic', 'university', 'money', 'click', 'market', 'our', 'business', 'today', 'advertise', 'product', 'company', 'sell', 'million', 'linguistics', 'english', 'internet', 'income', 'easy', 'save', 'guarantee', 'thousand', 'best', 'check', 'purchase', 'buy', 'cash', 'win', 'day', 'bulk', 'over', 'want', 'cost', 'dollar', 'every', '100', 'mailing', 'edu', 'service', 'll', 'com', 'yourself', 'papers', 'linguist', 'hundred', 'theory', 'earn', 'hour', 'customer', 'abstract', 'offer', 'profit', 'success', 'conference', 'fun', 'month', 'speaker', 'yours', 'here', 'watch', 'receive', 'pay', 'bonus', 'ever', 'syntax', 'discussion', 'amaze', 'credit', 'zip', 'start', 'sale', 'live', 'investment', 'toll', 'department', 'grammar', 'financial', 'anywhere', 'online', 'dream', 'science', 'huge', 'ad', 'deadline', 'structure', 'friend', 'simply', 'mlm', 'week', 'wait', 'need', 'workshop', 'study', 'fresh', 'security', 'analysis', 'marketing', 'xxx', 'topic', 'ship',

In [ ]:
feature_nums = [10, 100, 1000]
feature_t = []
for i in IG_dict_t:
  feature_t.append(i[0])
print(feature_t)
features_t = [0] * len(feature_nums)
print(features_t)
c = 0
for feature_num in feature_nums:
  features_t[c] = feature_t[:feature_num]
  c += 1
print(features_t[0])
print(features_t[1])
print(features_t[2])

['language', '1998', 'university', 'linguistic', 'papers', 'conference', 'remove', 'research', 'english', 'study', 'author', 'wait', 'click', 'll', 'workshop', 'abstract', 'sell', 'never', 'committee', 'discussion', 'enter', 'vacation', 'com', 'free', 'want', 'save', 'deadline', 'speaker', 'fax', 'structure', 'everyone', 'edu', 'student', 'online', 'theory', 'paper', 'approach', 'follow', 'offer', 'august', 'presentation', 'topic', 'advertisement', 'capitalfm', 'sale', 'secret', 'winner', 'aspect', 'reference', 'general', 'registration', 'science', 'today', 'win', 'institute', 'de', 'ticket', 'sorry', 'contact', 'our', 'linguistics', 'focus', 'two', 'model', 'participant', 'internet', 'present', 'album', 'chance', 'incredible', 'limited', 'monthly', 'pop', 'promotional', 'star', 'toll', 've', 'july', '15', 'page', 'aim', 'development', 'syntax', 'theoretical', 'invite', 'june', 'pick', 'form', 'release', 'trip', 'every', 'million', 'music', 'researcher', 'organize', 'reply', 'publish',

**get the frequency embedding matrix**

In [ ]:
vectorizer = CountVectorizer()
dt = vectorizer.fit_transform(train_data)
all_set = vectorizer.get_feature_names()
x = dt.toarray() 
index = [[] for i in range(len(feature_nums))]
c = 0
for feature in features:
  for i in feature:
    index[c].append(all_set.index(i))
  c += 1

embeds = [[] for i in range(len(feature_nums))]
c = 0
for c in range(len(feature_nums)):
  embeds[c] = x[:,index[c]]


In [ ]:
vectorizer = CountVectorizer()
dt_t = vectorizer.fit_transform(test_data)
all_set_t = vectorizer.get_feature_names()
x_t = dt_t.toarray() 
index_t = [[] for i in range(len(feature_nums))]
c = 0
for feature in features_t:
  for i in feature:
    index_t[c].append(all_set_t.index(i))
  c += 1
embeds_t = [[] for i in range(len(feature_nums))]
c = 0
for c in range(len(feature_nums)):
  embeds_t[c] = x_t[:,index_t[c]]

**featuren for frequency**




In [ ]:
train_x = embeds[2].tolist()
train_y = train_class
cc = list(zip(train_x, train_y))
random.shuffle(cc)
train_x[:], train_y[:] = zip(*cc)
# print(train_x)
# print(train_y)

In [ ]:
from sklearn.naive_bayes import MultinomialNB
clf = MultinomialNB().fit(train_x, train_y)


**featuren for binary**

**predict**

In [ ]:
y_pred = clf.predict(embeds_t[2])
y_pred = y_pred.tolist()

In [ ]:
correct = 0
wrong = 0
for i in range(len(y_pred)): 
  if y_pred[i] == test_class[j]:
      correct += 1
  elif y_pred[i] != test_class[j]:
      wrong += 1


268 23

In [ ]:
print(correct,wrong)

60 231
